In [2]:
%run Format.ipynb
import ROOT as root
from array import array
from math import sin
from ROOT import gRandom
from ROOT import TFile
from ROOT import TPad, TLegend
%jsroot on

Welcome to JupyROOT 6.29/01


In [3]:
N_centr =5
N_hists = 6
file_path="input/"
file_names="se-merge_18945_HeAu_Artem_raw_dphis.root"
histo_names = ["dphi_pt_cent_distr","dphi_min_pt_cent_distr","dphi_cnt_pt_cent_distr","dz_pt_cent_distr","dz_min_pt_cent_distr","dz_cnt_pt_cent_distr"]

In [4]:
hists_emc_read = []
infile = root.TFile.Open(file_path+file_names, "read")

for histname in histo_names:
    hists_emc_read.append(infile.Get(histname))
    hists_emc_read[-1].SetDirectory(root.nullptr)


infile.Close()

In [5]:
centrality = [1,-1,1,2,3,4,5,6,7,8]

pt = array( 'd' )
pt_boarders = array( 'd', [0.,.5,1.0,1.5,2.0,2.5,3.0,3.5,4.0,4.5,5.0,6.0,8.0,10.,20.])
pt_err = array( 'd' )
N_pt = len(pt_boarders) - 1
for i in range(N_pt):
    pt.append( (pt_boarders[i]+pt_boarders[i+1])/2)
    pt_err.append(0)
pt_boarders.append(20.)
print(pt,"\n",pt_boarders)

array('d', [0.25, 0.75, 1.25, 1.75, 2.25, 2.75, 3.25, 3.75, 4.25, 4.75, 5.5, 7.0, 9.0, 15.0]) 
 array('d', [0.0, 0.5, 1.0, 1.5, 2.0, 2.5, 3.0, 3.5, 4.0, 4.5, 5.0, 6.0, 8.0, 10.0, 20.0, 20.0])


In [48]:
boards_tot = [[-0.1,0.1],[-50,50]]
boards_fit = [[-0.02,0.02],[-8,8]]

def emc_fitter(InHist, centr, seed=1, fits_mean=0, fits_sigma=0):
    N_gaus=1
    seed0 = seed
    seed=seed*N_pt
    print(pt)

    hist_pt_bin = InHist.ProjectionY("kek")

    Mean_local =  array( 'd' )
    Sigma_local =  array( 'd' )
    Mean_local_err =  array( 'd' )
    Sigma_local_err =  array( 'd' )


    for p in range(N_pt):
        c1 = root.TCanvas(f"c1{seed+p}",f"c1{seed+p}",720,360)

        emc_var_porj = InHist.ProjectionX(f"emc{seed+p}",hist_pt_bin.FindBin(pt_boarders[p]),hist_pt_bin.FindBin(pt_boarders[p+1]),centrality[centr],centrality[centr+1])
        print("CENTRLITY :", centrality[centr], "-",centrality[centr+1])
        print("PT :", pt_boarders[p], "-",pt_boarders[p+1])
        print("bins :", pt_boarders[p], "-",pt_boarders[p+1])
        emc_var_porj.SetLineColor(1)

        par_tot = array( 'd', (3*N_gaus+3)*[2.] )
        g_gaus= root.TF1( f'g_gaus{seed+p}', 'gaus',  boards_fit[int(seed0/3)][0], boards_fit[int(seed0/3)][1])
        g_pol = root.TF1( f'g_pol{seed+p}', '[0]+[1]*x*(abs(x)/x-1)+[2]*x*(abs(x)/x+1)',  boards_tot[int(seed0/3)][0],boards_tot[int(seed0/3)][1])
        Format_Func(g_gaus,3,4)
        Format_Func(g_pol,3,2)

        total = root.TF1( f'total_pos{seed+p}', 'gaus(0)+[3]+[4]*x*(abs(x)/x-1)+[5]*x*(abs(x)/x+1)',boards_tot[int(seed0/3)][0], boards_tot[int(seed0/3)][1])
        Format_Func(total,2,1)


        if fits_mean!=0 and fits_sigma!=0:
            mean_ii=fits_mean.Eval(pt[p])
            sigma_ii=fits_sigma.Eval(pt[p])
            g_gaus.SetParameter(1,mean_ii)
            g_gaus.SetParameter(2,sigma_ii)
            g_gaus.SetParLimits(1,mean_ii*0.8-0.05,mean_ii*1.2+0.05)
            g_gaus.SetParLimits(2,sigma_ii*0.5,sigma_ii*1.5)
        else:
            g_gaus.SetParameter(1,0.)
            g_gaus.SetParameter(2,boards_fit[int(seed0/3)][1])


        #emc_var_porj.GetXaxis().SetRangeUser(-1.4, 0.5);
        emc_var_porj.Draw()
        emc_var_porj.Fit( g_gaus, 'QR')
        emc_var_porj.Fit( g_pol, 'QR+' )

        par_gaus = g_gaus.GetParameters()
        par_pol = g_pol.GetParameters()

        par_tot[0], par_tot[1], par_tot[2], par_tot[3], par_tot[4], par_tot[5] = par_gaus[0], par_gaus[1], par_gaus[2], par_pol[0], par_pol[1], par_pol[1]

        total.SetParameters( par_tot )
        total.SetParLimits(1,boards_tot[int(seed0/3)][0]/10,boards_tot[int(seed0/3)][1]/10)
        total.SetParLimits(2,boards_fit[int(seed0/3)][1]/10,boards_tot[int(seed0/3)][1]/2)
        
        emc_var_porj.Fit( total, 'R+' )


        Mean_local.append(total.GetParameter(1))
        Sigma_local.append(total.GetParameter(2))
        Mean_local_err.append(total.GetParError(1))
        Sigma_local_err.append(total.GetParError(2))
            


        #m2_pos.Draw("same") m2_neg.Draw("same")
        m2_name=str(seed0)+"/"+str(centr)+"/emc_"+str(round(pt[p],1))

        if fits_mean==0:
            c1.SaveAs( "output/" + m2_name + ".png" )
        else:
            c1.SaveAs( "output/" + m2_name + "upd.png" )

    return [Mean_local, Mean_local_err, Sigma_local, Sigma_local_err]


In [49]:
import multiprocess as mp

Ntr = N_hists

print([(hists_emc_read[i].GetName(), 0, i) for i in range(Ntr)])

pool = mp.Pool(Ntr)
output_array = pool.starmap(emc_fitter, [(hists_emc_read[i], 0, i) for i in range(Ntr)])
pool.close()

[('dphi_pt_cent_distr', 0, 0), ('dphi_min_pt_cent_distr', 0, 1), ('dphi_cnt_pt_cent_distr', 0, 2), ('dz_pt_cent_distr', 0, 3), ('dz_min_pt_cent_distr', 0, 4), ('dz_cnt_pt_cent_distr', 0, 5)]
array('d', [0.25, 0.75, 1.25, 1.75, 2.25, 2.75, 3.25, 3.75, 4.25, 4.75, 5.5, 7.0, 9.0, 15.0])
array('d', [0.25, 0.75, 1.25, 1.75, 2.25, 2.75, 3.25, 3.75, 4.25, 4.75, 5.5, 7.0, 9.0, 15.0])array('d', [0.25, 0.75, 1.25, 1.75, 2.25, 2.75, 3.25, 3.75, 4.25, 4.75, 5.5, 7.0, 9.0, 15.0])

array('d', [0.25, 0.75, 1.25, 1.75, 2.25, 2.75, 3.25, 3.75, 4.25, 4.75, 5.5, 7.0, 9.0, 15.0])
array('d', [0.25, 0.75, 1.25, 1.75, 2.25, 2.75, 3.25, 3.75, 4.25, 4.75, 5.5, 7.0, 9.0, 15.0])array('d', [0.25, 0.75, 1.25, 1.75, 2.25, 2.75, 3.25, 3.75, 4.25, 4.75, 5.5, 7.0, 9.0, 15.0])

CENTRLITY :CENTRLITY : 1 CENTRLITY : CENTRLITY :CENTRLITY :1  - 11 1    -1CENTRLITY :---
  -  PT :-1 1-1 -1-1
 

-
PT :0.0 PT :  -1PT :PT :- 
 PT :0.00.00.0    0.0  --0.5- 0.0 
  - 0.5bins : 0.5
0.5 0.5

-bins :
0.0bins :  bins :bins :  0.50.0 


Info in <TCanvas::Print>: png file output/4/0/emc_0.2.png has been created
Info in <TCanvas::Print>: png file output/3/0/emc_0.2.png has been created
Info in <TCanvas::Print>: png file output/2/0/emc_0.2.png has been created
Info in <TCanvas::Print>: png file output/1/0/emc_0.2.png has been created
Info in <TCanvas::Print>: png file output/0/0/emc_0.2.png has been created
Info in <TCanvas::Print>: png file output/5/0/emc_0.2.png has been created
Info in <TCanvas::Print>: png file output/3/0/emc_0.8.png has been created
Info in <TCanvas::Print>: png file output/4/0/emc_0.8.png has been created
Info in <TCanvas::Print>: png file output/2/0/emc_0.8.png has been created
Info in <TCanvas::Print>: png file output/1/0/emc_0.8.png has been created
Info in <TCanvas::Print>: png file output/0/0/emc_0.8.png has been created
Info in <TCanvas::Print>: png file output/5/0/emc_0.8.png has been created
Info in <TCanvas::Print>: png file output/3/0/emc_1.2.png has been created
Info in <TCanvas::Print>:

In [50]:
Means, Mean_errs, Sigmas, Sigma_errs = [], [], [], []
for i in range(Ntr):
    Means.append(output_array[i][0])
    Mean_errs.append(output_array[i][1])
    Sigmas.append(output_array[i][2])
    Sigma_errs.append(output_array[i][3])
print(Sigmas[1])
print(len(Sigmas))

array('d', [0.006339171428734542, 0.006235629158372439, 0.0049045516363642756, 0.004355034194687541, 0.003906609839344976, 0.003656035991865868, 0.003480619666932129, 0.0033595774118818688, 0.0034134867907581246, 0.0029880780702089566, 0.0032572689491835363, 0.0036914350745661626, 0.00315577801502255, 0.0020000005415103006])
6


In [51]:
with open('output/Mean.txt', 'w') as f:
#Mean.Write()
#Sigma.Write()
    for mean_centr in Means:
        for mean_part in mean_centr:
            f.write(f"{mean_part}\n")

with open('output/Sigma.txt', 'w') as f:
#Mean.Write()
#Sigma.Write()
    for sigma_centr in Sigmas:
        for sigma_part in sigma_centr:
            f.write(f"{sigma_part}\n")

In [78]:
fit_functions = []
for itype in range(N_hists):
    fit_functions_loc = []
    for icentr in range(N_centr):
        fit_functions_loc.append(root.TF1(f"fit_functions{itype}_{icentr}","(abs(x-[7])/(x-[7])+1)*([0]+[1]/x+[2]/x/x)+(abs(x-[7])/(x-[7])-1)*([4]+[5]*x+[6]*x*x)-(abs(x-4)/(x-4)+1)*([8]+[1]/x+[2]/x/x)"))
        fit_functions_loc[-1].FixParameter(7,0.8)
        fit_functions_loc[-1].FixParameter(3,0.0)
        fit_functions_loc[-1].SetLineWidth(3)
    fit_functions.append(fit_functions_loc)
print(fit_functions)

[[<cppyy.gbl.TF1 object at 0x562e436805a0>, <cppyy.gbl.TF1 object at 0x562e436b4e70>, <cppyy.gbl.TF1 object at 0x562e436b6fa0>, <cppyy.gbl.TF1 object at 0x562e435cc390>, <cppyy.gbl.TF1 object at 0x562e435cf5c0>], [<cppyy.gbl.TF1 object at 0x562e43692a30>, <cppyy.gbl.TF1 object at 0x562e43627850>, <cppyy.gbl.TF1 object at 0x562e4364f4a0>, <cppyy.gbl.TF1 object at 0x562e435f2720>, <cppyy.gbl.TF1 object at 0x562e43651a70>], [<cppyy.gbl.TF1 object at 0x562e436b9560>, <cppyy.gbl.TF1 object at 0x562e43658bf0>, <cppyy.gbl.TF1 object at 0x562e43629f60>, <cppyy.gbl.TF1 object at 0x562e4368ba90>, <cppyy.gbl.TF1 object at 0x562e436667c0>], [<cppyy.gbl.TF1 object at 0x562e4364cb20>, <cppyy.gbl.TF1 object at 0x562e43688100>, <cppyy.gbl.TF1 object at 0x562e436b7600>, <cppyy.gbl.TF1 object at 0x562e436bcf20>, <cppyy.gbl.TF1 object at 0x562e43656360>], [<cppyy.gbl.TF1 object at 0x562e43667a50>, <cppyy.gbl.TF1 object at 0x562e43503f90>, <cppyy.gbl.TF1 object at 0x562e436b0d90>, <cppyy.gbl.TF1 object at

In [79]:
h2=[]
c3 = root.TCanvas(f"c3",f"c3",500*3,500*2)
c3.Divide(3,2)
g_mean = [[[]]*N_centr]*N_hists
print(g_mean)
maxes = [0.01,0.01,0.02,5,5,10]
names = ["emc_r_dphi","emc_min_r_dphi","emc_cnt_dphi","emc_r_dz","emc_min_r_dz","emc_cnt_dz"]
legends =[]
for itype in range(N_hists):
    c3.cd(itype+1)
    h2.append(Format_Pad_old( 0.25, 16, 0, maxes[itype], "p_{T} (GeV/#it{c})", "Sigmas", 1.1, 1.1, 0.03, 0.03, "" ))
    h2[-1].Draw()
    legends.append(root.TLegend(0.3,0.5,0.7,0.9,names[itype]))
    legends[-1].SetFillColorAlpha(0,0)
    legends[-1].SetLineWidth(0)
    for icentr in range(0,N_centr-4):

        g_mean[itype][icentr].append(root.TGraphErrors(N_pt, pt, Sigmas[itype],pt_err,Sigma_errs[itype]))
        Format_Graph(g_mean[itype][icentr][-1],20,1, 4, 3, 4,1,1)
        g_mean[itype][icentr][-1].Fit( fit_functions[itype][icentr])
        #params_mean_sigma[syst][centr][0].append(all_fit_sigma_low[ii].GetParameters())
        g_mean[itype][icentr][-1].Draw('P')
        legends[-1].AddEntry(g_mean[itype][icentr][-1],f"0%-88%","p")
        legends[-1].AddEntry(fit_functions[itype][icentr],f"fit","l")
        
    legends[-1].Draw()
c3.Draw()
c3.SaveAs("output/emc_sigma.png")

[[[], [], [], [], []], [[], [], [], [], []], [[], [], [], [], []], [[], [], [], [], []], [[], [], [], [], []], [[], [], [], [], []]]
 FCN=22.3993 FROM HESSE     STATUS=NOT POSDEF     54 CALLS         311 TOTAL
                     EDM=1.7937e-16    STRATEGY= 1      ERR MATRIX NOT POS-DEF
  EXT PARAMETER                APPROXIMATE        STEP         FIRST   
  NO.   NAME      VALUE            ERROR          SIZE      DERIVATIVE 
   1  p0           1.02400e-03   8.20643e-06   5.58644e-10   2.41561e-03
   2  p1           2.85291e-03   2.29972e-05   7.46978e-10   1.72103e-03
   3  p2          -1.13112e-03   1.92886e-05   9.62220e-10   2.24613e-03
   4  p3           0.00000e+00     fixed    
   5  p4          -3.09964e-03   1.67540e-06   7.39011e-10   8.60523e-04
   6  p5          -1.17245e-03   8.43260e-06   2.79533e-10  -1.46159e-04
   7  p6           1.27732e-03   8.49323e-06   3.85172e-10  -3.14981e-04
   8  p7           8.00000e-01     fixed    
   9  p8          -6.65555e-04   2.6747

Warning in <TCanvas::Constructor>: Deleting canvas with same name: c3
Warning in <TROOT::Append>: Replacing existing TH1: sec (Potential memory leak).
Warning in <TROOT::Append>: Replacing existing TH1: sec (Potential memory leak).
Warning in <TROOT::Append>: Replacing existing TH1: sec (Potential memory leak).
Warning in <TROOT::Append>: Replacing existing TH1: sec (Potential memory leak).
Warning in <TROOT::Append>: Replacing existing TH1: sec (Potential memory leak).
Info in <TCanvas::Print>: png file output/emc_sigma.png has been created


In [ ]:
fit_mean_functions = []
for itype in range(N_hists):
    fit_mean_functions_loc = []
    for icentr in range(N_centr):
        fit_mean_functions_loc.append(root.TF1(f"fit_mean_functions{itype}_{icentr}","[0]+[1]*x+[2]/x+[3]*sqrt(x)+[4]*x*x",0.25,15))
        fit_mean_functions_loc[-1].SetLineWidth(3)
    fit_mean_functions.append(fit_functions_loc)
print(fit_mean_functions)

[[<cppyy.gbl.TF1 object at 0x5573a5d0d370>, <cppyy.gbl.TF1 object at 0x5573a5eed7e0>, <cppyy.gbl.TF1 object at 0x5573a5d6d480>, <cppyy.gbl.TF1 object at 0x5573a5eed400>, <cppyy.gbl.TF1 object at 0x5573a5ee0130>], [<cppyy.gbl.TF1 object at 0x5573a5d0d370>, <cppyy.gbl.TF1 object at 0x5573a5eed7e0>, <cppyy.gbl.TF1 object at 0x5573a5d6d480>, <cppyy.gbl.TF1 object at 0x5573a5eed400>, <cppyy.gbl.TF1 object at 0x5573a5ee0130>], [<cppyy.gbl.TF1 object at 0x5573a5d0d370>, <cppyy.gbl.TF1 object at 0x5573a5eed7e0>, <cppyy.gbl.TF1 object at 0x5573a5d6d480>, <cppyy.gbl.TF1 object at 0x5573a5eed400>, <cppyy.gbl.TF1 object at 0x5573a5ee0130>]]


In [ ]:
h3=[]
c4 = root.TCanvas(f"c4",f"c4",500*3,540)
c4.Divide(3,1)
g_mean = [[[]]*5]*3
print(g_mean)
colors = [1,2,4]
maxes = [0.001,0.001,0.002]
names = ["emc_r_dphi","emc_min_r_dphi","emc_cnt_dphi"]
legends =[]
for itype in range(N_hists):
    c4.cd(itype+1)
    h3.append(Format_Pad_old( 0.25, 16, -0.001, maxes[itype], "p_{T} (GeV/#it{c})", "Means", 1.1, 1.1, 0.03, 0.03, "" ))
    h3[-1].Draw()
    legends.append(root.TLegend(0.3,0.5,0.7,0.9,names[itype]))
    legends[-1].SetFillColorAlpha(0,0)
    legends[-1].SetLineWidth(0)
    for icentr in range(0,N_centr-4):

        g_mean[itype][icentr].append(root.TGraphErrors(N_pt, pt, Means[itype],pt_err,Mean_errs[itype]))
        Format_Graph(g_mean[itype][icentr][-1],20,1, 4, 3, 4,1,1)
        #g_mean[itype][icentr][-1].Fit( fit_mean_functions[itype][icentr],"M","r",1.,20)
        #params_mean_sigma[syst][centr][0].append(all_fit_sigma_low[ii].GetParameters())
        g_mean[itype][icentr][-1].Draw('P')
        legends[-1].AddEntry(g_mean[itype][icentr][-1],f"0%-88%","p")
        legends[-1].AddEntry(fit_functions[itype][icentr],f"fit","l")
        
    legends[-1].Draw()
c4.Draw()
c4.SaveAs("output/emc_mean.png")

[[[], [], [], [], []], [[], [], [], [], []], [[], [], [], [], []]]


Warning in <TCanvas::Constructor>: Deleting canvas with same name: c4
Warning in <TROOT::Append>: Replacing existing TH1: sec (Potential memory leak).
Warning in <TROOT::Append>: Replacing existing TH1: sec (Potential memory leak).
Info in <TCanvas::Print>: png file output/emc_mean.png has been created


In [ ]:
h2=[]
g_pos = [[[[] for j in range(6)] for k in range(N_centr)] for i in range(N_syst)] #part , low mean high
for syst in range(N_syst):
    c2 = root.TCanvas(f"c2{syst}",f"c2{syst}",1080,720)
    c2.Divide(3,2)
    for centr in range(N_centr):
        c2.cd(centr+1)
        h2.append(Format_Pad_old( 0.4, 3.9, -1., 1.5, "p_{T} (GeV/#it{c})", "Mean-2*Sigma", 1.1, 1.1, 0.03, 0.03, "" ))
        h2[-1].Draw()
        draw_part = [0,1,2,3,4,5,6]

        for i in range(3,6):
            ii = i+centr*7+syst*5*7
            part = draw_part[i]
            g_pos[syst][centr][i].append(root.TGraphErrors(n, pt, MeanTwoSigmaLow[syst][centr][part],pt_err,pt_err))
            Format_Graph(g_pos[syst][centr][i][-1],20,0, 2, 1, colors[i],1,1)
            g_pos[syst][centr][i][-1].Fit( all_fit_sigma_low[ii] ,"","",0.5,high_fit_range[i])
            params_mean_sigma[syst][centr][0].append(all_fit_sigma_low[ii].GetParameters())
            g_pos[syst][centr][i][-1].Draw('L')

            all_fit_sigma_low[ii].Draw('same')

            g_pos[syst][centr][i].append(root.TGraphErrors(n, pt, Mean[syst][centr][part],pt_err,pt_err))
            Format_Graph(g_pos[syst][centr][i][-1],20,0, 2, 1, colors[i],1,1)
            g_pos[syst][centr][i][-1].Draw('L')

            g_pos[syst][centr][i].append(root.TGraphErrors(n, pt, MeanTwoSigmaHigh[syst][centr][part],pt_err,pt_err))
            Format_Graph(g_pos[syst][centr][i][-1],20,0, 2, 1, colors[i],1,1)
            g_pos[syst][centr][i][-1].Fit( all_fit_sigma_high[ii] ,"","",0.5,high_fit_range[i])
            params_mean_sigma[syst][centr][1].append(all_fit_sigma_high[ii].GetParameters())
            g_pos[syst][centr][i][-1].Draw('L')

            all_fit_sigma_high[ii].Draw('same')

    c2.Draw()
    c2.SaveAs("output/m2_pos_fit_"+syst_names[syst]+".png")


****************************************
Minimizer is Minuit / Migrad
Chi2                      =  0.000387041
NDf                       =            6
Edm                       =  6.55735e-07
NCalls                    =          176
p0                        =  -0.00228508   +/-   0.0323749   
p1                        =      139.538   +/-   41277.6     
p2                        =          104                      	 (fixed)
p3                        =      -2.4456   +/-   22667.5     
p4                        =  1.30767e-10   +/-   9.2954e-12  
p5                        =  2.99792e+08                      	 (fixed)
p6                        =         4.95                      	 (fixed)

****************************************
Minimizer is Minuit / Migrad
Chi2                      =  5.56124e-06
NDf                       =            6
Edm                       =  2.44235e-06
NCalls                    =          254
p0                        =     0.104136   +/-   0.00515669  
p1  

Warning in <TROOT::Append>: Replacing existing TH1: sec (Potential memory leak).
Warning in <TROOT::Append>: Replacing existing TH1: sec (Potential memory leak).
Warning in <TROOT::Append>: Replacing existing TH1: sec (Potential memory leak).
Warning in <TROOT::Append>: Replacing existing TH1: sec (Potential memory leak).
Info in <TCanvas::Print>: png file output/m2_pos_fit_pp.png has been created
Warning in <TROOT::Append>: Replacing existing TH1: sec (Potential memory leak).
Warning in <TROOT::Append>: Replacing existing TH1: sec (Potential memory leak).
Warning in <TROOT::Append>: Replacing existing TH1: sec (Potential memory leak).
Warning in <TROOT::Append>: Replacing existing TH1: sec (Potential memory leak).
Warning in <TROOT::Append>: Replacing existing TH1: sec (Potential memory leak).
Warning in <Fit>: Abnormal termination of minimization.
Info in <TCanvas::Print>: png file output/m2_pos_fit_pAl.png has been created
Warning in <TROOT::Append>: Replacing existing TH1: sec (Pot

In [ ]:
print(len(params_mean_sigma),len(params_mean_sigma[0]),len(params_mean_sigma[0][0]),len(params_mean_sigma[0][0][0]),params_mean_sigma[0][0][0][0])
with open('output/Parameters_Mean_Sigma.txt', 'w') as f:

    for par_lh in params_mean_sigma:
        for par_part in par_lh:
            for par_par in par_part:
                f.write(f"{par_par}\n")

3 5 2 6 <cppyy.LowLevelView object at 0x7f8fe7fd4420>


In [ ]:
import multiprocess as mp
n=n+1
pt.append(4.0)
Ntr = N_syst*N_centr
pool = mp.Pool(Ntr)
output_array = pool.starmap(m2_fitter, [(i//N_centr, i%N_centr*2, i, all_fit_sigma_low, all_fit_sigma_high) for i in range(N_syst*N_centr)])
pool.close()
pt.pop()
n=n-1

array('d', [0.3, 0.4, 0.5, 0.6000000000000001, 0.7, 0.8, 0.9000000000000001, 1.0, 1.1, 1.2, 1.3, 1.4000000000000001, 1.5000000000000002, 1.6, 1.7000000000000002, 1.8, 1.9000000000000001, 2.0, 2.1, 2.2, 2.3, 2.4, 2.5, 2.6, 2.7, 2.8, 2.9, 3.0, 3.1, 3.2, 3.3, 3.4, 3.5, 3.6, 3.7, 3.8, 3.9, 4.0])
se-merge17354pp.root 
 CENTRLITY : 1 - -1

 PT : 0.3 - 0.4
se-merge17354pp.rootarray('d', [0.3, 0.4, 0.5, 0.6000000000000001, 0.7, 0.8, 0.9000000000000001, 1.0, 1.1, 1.2, 1.3, 1.4000000000000001, 1.5000000000000002, 1.6, 1.7000000000000002, 1.8, 1.9000000000000001, 2.0, 2.1, 2.2, 2.3, 2.4, 2.5, 2.6, 2.7, 2.8, 2.9, 3.0, 3.1, 3.2, 3.3, 3.4, 3.5, 3.6, 3.7, 3.8, 3.9, 4.0]) 
 CENTRLITY :
 1 - -1

 PT : 0.4 - 0.5
se-merge17354pp.root 
 CENTRLITY : 1 - 2

 PT : 0.3 - 0.4
se-merge17354pp.root 
 CENTRLITY : 1 - -1

 PT : 0.5 - 0.6000000000000001
array('d', [0.3, 0.4, 0.5, 0.6000000000000001, 0.7, 0.8, 0.9000000000000001, 1.0, 1.1, 1.2, 1.3, 1.4000000000000001, 1.5000000000000002, 1.6, 1.7000000000000002, 1.

IOPub message rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_msg_rate_limit`.

Current values:
NotebookApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
NotebookApp.rate_limit_window=3.0 (secs)



2
 2.9 - 3.0
se-merge16689_pAl.rootse-merge17280pAu.root  
 CENTRLITY :
 CENTRLITY :  11  -se-merge16689_pAl.root-   2
 CENTRLITY :-1

 PT : 
5
 PT :   2.4-  -6
 1.5000000000000002
 PT :2.5 se-merge17280pAu.root 
- 2.3  
 CENTRLITY :1.6- 
 52.4 - 
6se-merge17280pAu.root
 
 PT :
 CENTRLITY : 0.9000000000000001  7- se-merge16689_pAl.root  1.0
 CENTRLITY :-
  87

 PT :  -0.8  8- 
0.9000000000000001
 PT :
 2.3 - 2.4
se-merge17280pAu.root 
 CENTRLITY : 3 - 4se-merge17280pAu.root
 
 PT :
 CENTRLITY :  11.1  -- 2
 
 PT :1.2 
1.3 -se-merge16689_pAl.root  1.4000000000000001

 CENTRLITY : 3 - 4

 PT : 2.4 - 2.5
se-merge16689_pAl.root 
 CENTRLITY : 1 - -1

 PT : 2.5 -se-merge16689_pAl.root  2.6
 CENTRLITY :
 7 - 8

 PT : 2.4 - 2.5
se-merge17280pAu.rootse-merge17280pAu.root  
 CENTRLITY :
 CENTRLITY : 5 1  --  -16se-merge17280pAu.root
 
 PT :
 
 CENTRLITY : 
 PT :1.0  7-1.6  -1.1  
8-
 
 PT :1.7000000000000002
 0.9000000000000001 - 1.0se-merge17354pp.root
 
 CENTRLITY : 1 - -1

 PT : 3.1 - 3.2
se-

IOPub message rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_msg_rate_limit`.

Current values:
NotebookApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
NotebookApp.rate_limit_window=3.0 (secs)



se-merge17280pAu.root 
 CENTRLITY : 7 - 8

 PT : 3.9 - 4.0
se-merge17280pAu.root 
 CENTRLITY : 3se-merge17280pAu.root  -
 CENTRLITY :  45
 -
 PT :  63.6
 
 PT :-  3.73.5
 - 3.6
se-merge17280pAu.root 
 CENTRLITY : 1 - se-merge17280pAu.root-1 

 CENTRLITY :
 PT :  13.6  - 3.7
- 2se-merge17280pAu.root
 
 PT :
 CENTRLITY :  3.53 -  -3.6 
4

 PT : 3.7se-merge17280pAu.root -  
 CENTRLITY :3.8 
5 - 6

 PT : 3.6 - 3.7
se-merge17280pAu.root 
 CENTRLITY : 1 - 2

 PT : 3.6 - 3.7
se-merge17280pAu.root 
 CENTRLITY : 5 - 6

 PT : 3.7 - 3.8
se-merge17280pAu.root
 CENTRLITY :  3 - 4

 PT : 3.8 - 3.9
se-merge17280pAu.root 
 CENTRLITY : 1 - -1

 PT : 3.7 - 3.8
se-merge17280pAu.root 
 CENTRLITY : 5 - 6

 PT : 3.8 - 3.9
se-merge17280pAu.root 
 CENTRLITY : 3 - 4

 PT : 3.9 - 4.0
se-merge17280pAu.root 
 CENTRLITY : 1 - 2

 PT : 3.7 - 3.8
se-merge17280pAu.root 
 CENTRLITY : 5 - 6

 PT : 3.9 - 4.0
se-merge17280pAu.root 
 CENTRLITY :se-merge17280pAu.root  1
 CENTRLITY :  -1  2

 PT :- -1 
3.8
 PT :  -3.8  3.9-

Info in <ROOT::Math::ParameterSettings>: lower/upper bounds outside current parameter value. The value will be set to (low+up)/2 
Info in <ROOT::Math::ParameterSettings>: lower/upper bounds outside current parameter value. The value will be set to (low+up)/2 
Info in <TCanvas::Print>: png file output/pp/0/m2_0.3upd.png has been created
Info in <ROOT::Math::ParameterSettings>: lower/upper bounds outside current parameter value. The value will be set to (low+up)/2 
Info in <ROOT::Math::ParameterSettings>: lower/upper bounds outside current parameter value. The value will be set to (low+up)/2 
Info in <TCanvas::Print>: png file output/pp/0/m2_0.4upd.png has been created
Info in <ROOT::Math::ParameterSettings>: lower/upper bounds outside current parameter value. The value will be set to (low+up)/2 
Info in <ROOT::Math::ParameterSettings>: lower/upper bounds outside current parameter value. The value will be set to (low+up)/2 
Info in <ROOT::Math::ParameterSettings>: lower/upper bounds outs

In [ ]:
for i in range(0, Ntr):
    print(i//N_centr, i%N_centr)
    Mean[i//N_centr][i%N_centr]=output_array[i][0]
    Sigma[i//N_centr][i%N_centr]=output_array[i][1]
print(Mean)

0 0
0 1
0 2
0 3
0 4
1 0
1 1
1 2
1 3
1 4
2 0
2 1
2 2
2 3
2 4
[[[array('d', [-0.9466505538112682, -0.9444084945357906, -0.9126145088268364, -0.8994645853445878, -0.8949892626982856, -0.8936474921838616, -0.8939558040907087, -0.8936559590684914, -0.8940689517943043, -0.8946717512066296, -0.8958345858965412, -0.8981054089016443, -0.8972280583310817, -0.8960839310294877, -0.8971075850638602, -0.8990346408558327, -0.8987888329135181, -0.9022002446075157, -0.9011338110558634, -0.9008755341880342, -0.901532627559875, -0.895557336621455, -0.8999908073541182, -0.8936354268891074, -0.8968510506798517, -0.8979733727810653, -0.8780068493150688, -0.8704358974358977, -0.8878299999999999, -0.8798756613756611, -0.8572186440677965, -0.8586826484018263, -0.8597523364485979, -0.8449019607843138, -0.8466000000000002, -0.8334308176100629, -0.842515503875969]), array('d', [-0.24436075948599373, -0.2456113993087098, -0.2461369876762732, -0.2455850317950007, -0.24528989983230412, -0.24508949797012955, -0.24473

In [ ]:
with open('output/Mean1.txt', 'w') as f:
    #Mean.Write()
    #Sigma.Write()
    for mean_centr in Mean:
        for mean_part in mean_centr:
            for mean_pt in mean_part:
                f.write(f"{mean_pt}\n")

with open('output/Sigma1.txt', 'w') as f:
    #Mean.Write()
    #Sigma.Write()
    for sigma_centr in Sigma:
        for sigma_part in sigma_centr:
            for sigma_pt in sigma_part:
                f.write(f"{sigma_pt}\n")

In [ ]:
pt_err = array('d')
MeanTwoSigmaLow = [[[array("d") for j in range(6)] for i in range(5)] for k in range(N_syst)]
MeanTwoSigmaHigh = [[[array("d") for j in range(6)] for i in range(5)] for k in range(N_syst)]

for a in range(n):
    pt_err.append(0)
print(len(Mean), "\n")
print(len(Mean[0]), "\n")
print(len(Mean[0][0]), "\n")

for i in range(N_syst):
    for j in range(N_centr):
        for k in range(N_part):
            for l in range(N_pt):
                MeanTwoSigmaLow[i][j][k].append(Mean[i][j][k][l] - 2 * Sigma[i][j][k][l])
                MeanTwoSigmaHigh[i][j][k].append(Mean[i][j][k][l] + 2 * Sigma[i][j][k][l])

3 

5 

6 



In [ ]:
h2=[]
g_negativ = [[[[] for j in range(3)] for k in range(N_centr)] for i in range(N_syst)] #part , low mean high
for syst in range(N_syst):
    c2 = root.TCanvas(f"c2{syst}",f"c2{syst}",1400,2000)
    c2.Divide(2,3)
    for centr in range(N_centr):
        c2.cd(centr+1)
        h2.append(Format_Pad_old( 0.4, 3.9, -1.5, 1, "p_{T} (GeV/#it{c})", "Mean-2*Sigma", 1.1, 1.1, 0.03, 0.03, "" ))
        h2[-1].Draw()
        draw_part = [0,1,2,6]

        for i in range(3):
            ii = i+centr*7+syst*5*7
            part = draw_part[i]
            g_negativ[syst][centr][i].append(root.TGraphErrors(n, pt, MeanTwoSigmaLow[syst][centr][part],pt_err,pt_err))
            Format_Graph(g_negativ[syst][centr][i][-1],20,0, 2, 1, colors[i],1,1)
            g_negativ[syst][centr][i][-1].Fit( all_fit_sigma_low[ii] ,"","",0.5,high_fit_range[i])
            params_mean_sigma[syst][centr][0].append(all_fit_sigma_low[ii].GetParameters())
            g_negativ[syst][centr][i][-1].Draw('L')

            all_fit_sigma_low[ii].Draw('same')

            g_negativ[syst][centr][i].append(root.TGraphErrors(n, pt, Mean[syst][centr][part],pt_err,pt_err))
            Format_Graph(g_negativ[syst][centr][i][-1],20,0, 2, 1, colors[i],1,1)
            g_negativ[syst][centr][i][-1].Draw('L')

            g_negativ[syst][centr][i].append(root.TGraphErrors(n, pt, MeanTwoSigmaHigh[syst][centr][part],pt_err,pt_err))
            Format_Graph(g_negativ[syst][centr][i][-1],20,0, 2, 1, colors[i],1,1)
            g_negativ[syst][centr][i][-1].Fit( all_fit_sigma_high[ii] ,"","",0.5,high_fit_range[i])
            params_mean_sigma[syst][centr][1].append(all_fit_sigma_high[ii].GetParameters())
            g_negativ[syst][centr][i][-1].Draw('L')

            all_fit_sigma_high[ii].Draw('same')

    c2.Draw()
    c2.SaveAs("output/m2_neg_fit_"+syst_names[syst]+"upd.png")


****************************************
Minimizer is Minuit / Migrad
Chi2                      =    0.0100338
NDf                       =           17
Edm                       =  3.08028e-07
NCalls                    =          204
p0                        =    -0.919849   +/-   0.0160852   
p1                        =    0.0658866   +/-   5.22285     
p2                        =          104                      	 (fixed)
p3                        =      2.39383   +/-   0.742841    
p4                        =  2.89438e-10   +/-   2.2523e-11  
p5                        =  2.99792e+08                      	 (fixed)
p6                        =         4.95                      	 (fixed)

****************************************
Minimizer is Minuit / Migrad
Chi2                      =    0.0130657
NDf                       =           17
Edm                       =  9.49273e-07
NCalls                    =           99
p0                        =    -0.960174   +/-   0.0156969   
p1  

Warning in <Fit>: Abnormal termination of minimization.
Warning in <TROOT::Append>: Replacing existing TH1: sec (Potential memory leak).
Warning in <Fit>: Abnormal termination of minimization.
Warning in <TROOT::Append>: Replacing existing TH1: sec (Potential memory leak).
Warning in <Fit>: Abnormal termination of minimization.
Warning in <Fit>: Abnormal termination of minimization.
Warning in <TROOT::Append>: Replacing existing TH1: sec (Potential memory leak).
Warning in <Fit>: Abnormal termination of minimization.
Warning in <Fit>: Abnormal termination of minimization.
Warning in <TROOT::Append>: Replacing existing TH1: sec (Potential memory leak).
Warning in <Fit>: Abnormal termination of minimization.
Warning in <Fit>: Abnormal termination of minimization.
Info in <TCanvas::Print>: png file output/m2_neg_fit_ppupd.png has been created
Warning in <TROOT::Append>: Replacing existing TH1: sec (Potential memory leak).
Warning in <TROOT::Append>: Replacing existing TH1: sec (Potential 

In [ ]:
h2=[]
g_pos = [[[[] for j in range(6)] for k in range(N_centr)] for i in range(N_syst)] #part , low mean high
for syst in range(N_syst):
    c2 = root.TCanvas(f"c2{syst}",f"c2{syst}",1400,2000)
    c2.Divide(2,3)
    for centr in range(N_centr):
        c2.cd(centr+1)
        h2.append(Format_Pad_old( 0.4, 3.9, -1., 1.5, "p_{T} (GeV/#it{c})", "Mean-2*Sigma", 1.1, 1.1, 0.03, 0.03, "" ))
        h2[-1].Draw()
        draw_part = [0,1,2,3,4,5,6]

        for i in range(3,6):
            ii = i+centr*7+syst*5*7
            part = draw_part[i]
            g_pos[syst][centr][i].append(root.TGraphErrors(n, pt, MeanTwoSigmaLow[syst][centr][part],pt_err,pt_err))
            Format_Graph(g_pos[syst][centr][i][-1],20,0, 2, 1, colors[i],1,1)
            g_pos[syst][centr][i][-1].Fit( all_fit_sigma_low[ii] ,"","",0.5,high_fit_range[i])
            params_mean_sigma[syst][centr][0].append(all_fit_sigma_low[ii].GetParameters())
            g_pos[syst][centr][i][-1].Draw('L')

            all_fit_sigma_low[ii].Draw('same')

            g_pos[syst][centr][i].append(root.TGraphErrors(n, pt, Mean[syst][centr][part],pt_err,pt_err))
            Format_Graph(g_pos[syst][centr][i][-1],20,0, 2, 1, colors[i],1,1)
            g_pos[syst][centr][i][-1].Draw('L')

            g_pos[syst][centr][i].append(root.TGraphErrors(n, pt, MeanTwoSigmaHigh[syst][centr][part],pt_err,pt_err))
            Format_Graph(g_pos[syst][centr][i][-1],20,0, 2, 1, colors[i],1,1)
            g_pos[syst][centr][i][-1].Fit( all_fit_sigma_high[ii] ,"","",0.5,high_fit_range[i])
            params_mean_sigma[syst][centr][1].append(all_fit_sigma_high[ii].GetParameters())
            g_pos[syst][centr][i][-1].Draw('L')

            all_fit_sigma_high[ii].Draw('same')

    c2.Draw()
    c2.SaveAs("output/m2_pos_fit_"+syst_names[syst]+".png")


****************************************
Minimizer is Minuit / Migrad
Chi2                      =  5.68661e-06
NDf                       =            6
Edm                       =  8.56807e-09
NCalls                    =          299
p0                        =     0.113547   +/-   0.00124192  
p1                        =  0.000780582   +/-   0.00137678  
p2                        =          104                      	 (fixed)
p3                        =  2.28666e-08   +/-   0.00137678  
p4                        =  1.71147e-10   +/-   1.42595e-12 
p5                        =  2.99792e+08                      	 (fixed)
p6                        =         4.95                      	 (fixed)

****************************************
Minimizer is Minuit / Migrad
Chi2                      =  4.74969e-06
NDf                       =            6
Edm                       =  9.90435e-07
NCalls                    =           75
p0                        =     0.104213   +/-   0.00477697  
p1  

Warning in <TROOT::Append>: Replacing existing TH1: sec (Potential memory leak).
Warning in <TROOT::Append>: Replacing existing TH1: sec (Potential memory leak).
Warning in <TROOT::Append>: Replacing existing TH1: sec (Potential memory leak).
Warning in <Fit>: Abnormal termination of minimization.
Warning in <Fit>: Abnormal termination of minimization.
Warning in <TROOT::Append>: Replacing existing TH1: sec (Potential memory leak).
Warning in <Fit>: Abnormal termination of minimization.
Warning in <Fit>: Abnormal termination of minimization.
Warning in <TROOT::Append>: Replacing existing TH1: sec (Potential memory leak).
Warning in <Fit>: Abnormal termination of minimization.
Warning in <Fit>: Abnormal termination of minimization.
Info in <TCanvas::Print>: png file output/m2_pos_fit_pp.png has been created
Warning in <TROOT::Append>: Replacing existing TH1: sec (Potential memory leak).
Warning in <TROOT::Append>: Replacing existing TH1: sec (Potential memory leak).
Warning in <TROOT::A

In [ ]:
Yield = [[[array("d") for i in range(N_part)] for j in range(N_centr)] for k in range(N_syst)]
pt.append(4.0)
for syst in range(N_syst):
    for centr in range(N_centr):
        for p in range(N_pt):
            m2_pos = tof_m2_pt_pos[syst].ProjectionY("m2_pos",pt_hist_pos[syst].FindBin(pt[p]),pt_hist_pos[syst].FindBin(pt[p+1]),centrality[2*centr],centrality[2*centr+1])
            m2_neg = tof_m2_pt_neg[syst].ProjectionY("m2_neg",pt_hist_neg[syst].FindBin(pt[p]),pt_hist_neg[syst].FindBin(pt[p+1]),centrality[2*centr],centrality[2*centr+1])

            for part1 in range(0,3):
                ii = part1+0*centr*7+70+0*syst*5*7
                if part1 == 0:
                    l=all_fit_sigma_low[ii].Eval(pt[p])
                    h=min(all_fit_sigma_high[ii].Eval(pt[p]),all_fit_sigma_low[ii+1].Eval(pt[p]))
                elif part1 == 1:
                    l=max(all_fit_sigma_low[ii].Eval(pt[p]),all_fit_sigma_high[ii-1].Eval(pt[p]))
                    h=min(all_fit_sigma_high[ii].Eval(pt[p]),all_fit_sigma_low[ii+1].Eval(pt[p]))
                else:
                    l=max(all_fit_sigma_low[ii].Eval(pt[p]),all_fit_sigma_high[ii-1].Eval(pt[p]))
                    h=all_fit_sigma_high[ii].Eval(pt[p])
                if h>l:
                    Yield[syst][centr][part1].append(m2_neg.Integral(m2_neg.FindBin(l),m2_neg.FindBin(h)))
                elif syst == 0:
                    Yield[syst][centr][part1].append(1000)
                else:
                    Yield[syst][centr][part1].append(0)

            for part2 in range(3,6):
                ii = part2+0*centr*7+syst*5*7
                if part2 == 0:
                    l=all_fit_sigma_low[ii].Eval(pt[p])
                    h=min(all_fit_sigma_high[ii].Eval(pt[p]),all_fit_sigma_low[ii+1].Eval(pt[p]))
                elif part2 == 1:
                    l=max(all_fit_sigma_low[ii].Eval(pt[p]),all_fit_sigma_high[ii-1].Eval(pt[p])-100)
                    h=min(all_fit_sigma_high[ii].Eval(pt[p]),all_fit_sigma_low[ii+1].Eval(pt[p]))
                else:
                    l=max(all_fit_sigma_low[ii].Eval(pt[p]),all_fit_sigma_high[ii-1].Eval(pt[p]))
                    h=all_fit_sigma_high[ii].Eval(pt[p])
                Yield[syst][centr][part2].append(m2_pos.Integral(m2_pos.FindBin(l),m2_neg.FindBin(h)))

print(len(Yield),len(Yield[0]),len(Yield[0][0]),len(Yield[0][0][0]),"\n")
#print(Yield[1][0][3],Yield[1][1][3],Yield[1][3][3])
pt.pop()
print(pt)

3 5 6 37 

array('d', [0.3, 0.4, 0.5, 0.6000000000000001, 0.7, 0.8, 0.9000000000000001, 1.0, 1.1, 1.2, 1.3, 1.4000000000000001, 1.5000000000000002, 1.6, 1.7000000000000002, 1.8, 1.9000000000000001, 2.0, 2.1, 2.2, 2.3, 2.4, 2.5, 2.6, 2.7, 2.8, 2.9, 3.0, 3.1, 3.2, 3.3, 3.4, 3.5, 3.6, 3.7, 3.8, 3.9])


In [ ]:
RAB = [[[array("d") for i in range(N_part)] for j in range(N_centr)] for k in range(N_syst)]
RAB_stat = [[[array("d") for i in range(N_part)] for j in range(N_centr)] for k in range(N_syst)]
centr_bin=[1,100,1,20,21,40,41,60,61,84,81,100]
fbias=[[0.8,0.81,0.9,0.99,1.15],[0.858,0.90,0.98,1.02,1.0]]
Ncoll=[[2.1,3.4,2.3,1.8,1.3],[4.7,8.2,6.1,4.4,2.6]]
Nev_pAl=[]
Nev_pAu=[]
for i in range(N_centr):
    Nev_pAl.append(central_bin[1].Integral(centr_bin[2*i],centr_bin[2*i+1])+1)
    Nev_pAu.append(central_bin[2].Integral(centr_bin[2*i],centr_bin[2*i+1]))
Nev=[Nev_pAl,Nev_pAu]
bias_pp=0.73/0.55
Nev_pp=central_bin[0].GetEntries()
print(Nev_pp,Nev)

podgon=(tof_zedphi_pip[1].Integral()/tof_zedphi_pip[2].Integral())/(dc_all[1].Integral()/dc_all[2].Integral())
print(tof_zedphi_pip[0].Integral()/dc_all[0].Integral(),tof_zedphi_pip[1].Integral()/dc_all[1].Integral(),tof_zedphi_pip[2].Integral()/dc_all[2].Integral())
pro_podgon=[1,1,podgon]

for syst in range(1,N_syst):
    for centr in range(N_centr):
        for part in range(N_part):
            for p in range(N_pt):
                RAB[syst][centr][part].append(Yield[syst][centr][part][p]/Yield[0][0][part][p]/Nev[syst-1][centr]*Nev_pp*fbias[syst-1][centr]/bias_pp/Ncoll[syst-1][centr]/pro_podgon[syst])
                RAB_stat[syst][centr][part].append(RAB[syst][centr][part][-1]*((1/(Yield[syst][centr][part][p]+1)+1.0/Yield[0][0][part][p])**(1./2)))

2605350843.0 [[531092710.0, 153685092.0, 148056753.0, 145067430.0, 84283438.0], [1119621284.0, 269991205.0, 267425497.0, 266408702.0, 315795880.0]]
0.5650358139072199 0.3823664015877239 0.563316535829536


In [ ]:
h_rab=[]
graph = [[[] for k in range(N_centr)] for i in range(N_syst)] #part , low mean high
legend=[]
c4=[]
for syst in range(1,N_syst):
    c4.append(root.TCanvas(f"c4{syst}",f"c4{syst}",1080,720))
    c4[-1].Divide(3,2)
    for centr in range(N_centr):
        c4[-1].cd(centr+1)
        h_rab.append(Format_Pad_old( 0.4, 4.0, 0.1, 1.9, "p_{T} (GeV/#it{c})", "Mean-2*Sigma", 1.1, 1.1, 0.03, 0.03, "" ))
        h_rab[-1].Draw()

        legend.append(root.TLegend(0.7,0.7,0.95,0.95))
        for part in range(0,3):
            graph[syst][centr].append(root.TGraphErrors(N_pt, pt, RAB[syst][centr][part],pt_err,RAB_stat[syst][centr][part]))
            Format_Graph(graph[syst][centr][-1],17+part,0.5, colors[part], 1, colors[part],1,1)
            graph[syst][centr][-1].Draw('same')
            legend[-1].AddEntry(graph[syst][centr][-1],particles[part],"p")

        legend[-1].Draw('same')

    c4[-1].Draw()
    c4[-1].SaveAs("output/rab"+syst_names[syst]+".png")

Warning in <TROOT::Append>: Replacing existing TH1: sec (Potential memory leak).
Warning in <TROOT::Append>: Replacing existing TH1: sec (Potential memory leak).
Warning in <TROOT::Append>: Replacing existing TH1: sec (Potential memory leak).
Warning in <TROOT::Append>: Replacing existing TH1: sec (Potential memory leak).
Warning in <TROOT::Append>: Replacing existing TH1: sec (Potential memory leak).
Info in <TCanvas::Print>: png file output/rabpAl.png has been created
Warning in <TROOT::Append>: Replacing existing TH1: sec (Potential memory leak).
Warning in <TROOT::Append>: Replacing existing TH1: sec (Potential memory leak).
Warning in <TROOT::Append>: Replacing existing TH1: sec (Potential memory leak).
Warning in <TROOT::Append>: Replacing existing TH1: sec (Potential memory leak).
Warning in <TROOT::Append>: Replacing existing TH1: sec (Potential memory leak).
Info in <TCanvas::Print>: png file output/rabpAu.png has been created
